In [134]:
from itertools import chain

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import yfinance as yf

from funcs import *

In [135]:
pd.set_option('plotting.backend', "plotly")

In [136]:
msci_world_gross = read_msci_data('data/MSCI World USD Gross.xls')

In [137]:
msci_world_net = read_msci_data('data/MSCI World USD Net.xls')

In [138]:
msci_world = msci_world_gross.pct_change().add(msci_world_net.pct_change()).div(2).add(1).cumprod().mul(100).fillna(100)

In [139]:
sti = pd.read_csv('data/Straits Times Index USD Gross.csv', parse_dates=['Date'])[['Date', 'Close']]

In [140]:
sti_1m = sti.rename({'Date': 'date', 'Close': 'price'}, axis=1).set_index('date').resample('BM').last().iloc[:-1]

In [141]:
fed_funds_rate, fed_funds_rate_1m = load_fed_funds_rate()

In [142]:
sp500: pd.DataFrame = yf.download('^SP500TR')['Adj Close']

[*********************100%%**********************]  1 of 1 completed


In [143]:
sp500 = sp500.resample('BM').last()

In [144]:
shiller_sp500 = read_shiller_sp500_data(net=True)

In [145]:
usdsgd_monthly = download_usdsgd_monthly()

In [146]:
usdsgd_daily = download_usdsgd_daily()

In [147]:
sgd_interest_rates, sgd_interest_rates_1m = load_sgd_interest_rates()

In [148]:
sg_cpi = load_sg_cpi()

In [149]:
us_cpi = load_us_cpi()

In [150]:
msci_world = msci_world.merge(fed_funds_rate_1m, left_index=True, right_index=True, how='left')

In [151]:
msci_world = msci_world.merge(sgd_interest_rates_1m['sgd_ir_1m'], left_index=True, right_index=True, how='left')

In [152]:
periods = ['1m', '3m', '6m', '1y', '2y', '3y', '5y', '10y', '15y', '20y', '25y', '30y']
durations = [1, 3, 6, 12, 24, 36, 60, 120, 180, 240, 300, 360]

In [153]:
add_return_columns(msci_world, periods, durations)

In [154]:
add_return_columns(sti_1m, periods, durations)

In [155]:
add_return_columns(shiller_sp500, periods, durations)

In [156]:
msci_world.head(10)

price        ffr  sgd_ir_1m  1m_cumulative  3m_cumulative  \
date                                                                         
1969-12-31  100.000000  10.391636        NaN            NaN            NaN   
1970-01-30   94.491500   9.376079        NaN      -0.055085            NaN   
1970-02-27   97.481485   8.771530        NaN       0.031643            NaN   
1970-03-31   97.827451   8.657911        NaN       0.003549      -0.021725   
1970-04-30   88.727406   8.432125        NaN      -0.093021      -0.061001   
1970-05-29   83.173339   7.988168        NaN      -0.062597      -0.146778   
1970-06-30   81.167249   8.469048        NaN      -0.024119      -0.170302   
1970-07-31   86.244611   7.739472        NaN       0.062554      -0.027982   
1970-08-31   89.130958   7.074040        NaN       0.033467       0.071629   
1970-09-30   92.051783   6.491091        NaN       0.032770       0.134100   

            6m_cumulative  1y_cumulative  2y_cumulative  3y_cumulative  \
date                                                                     
1969-12-31            NaN            NaN            NaN            NaN   
1970-01-30            NaN            NaN            NaN            NaN   
1970-02-27            NaN            NaN            NaN            NaN   
1970-03-31            NaN            NaN            NaN            NaN   
1970-04-30            NaN            NaN            NaN            NaN   
1970-05-29            NaN            NaN            NaN            NaN   
1970-06-30      -0.188328            NaN            NaN            NaN   
1970-07-31      -0.087277            NaN            NaN            NaN   
1970-08-31      -0.085663            NaN            NaN            NaN   
1970-09-30      -0.059039            NaN            NaN            NaN   

            5y_cumulative  ...  6m_difference_in_annualized  \
date                       ...                                
1969-12-31            NaN  ...                          NaN   
1970-01-30            NaN  ...                          NaN   
1970-02-27            NaN  ...                          NaN   
1970-03-31            NaN  ...                          NaN   
1970-04-30            NaN  ...                          NaN   
1970-05-29            NaN  ...                          NaN   
1970-06-30            NaN  ...                    -0.099155   
1970-07-31            NaN  ...                    -0.085514   
1970-08-31            NaN  ...                    -0.175085   
1970-09-30            NaN  ...                    -0.223886   

            1y_difference_in_annualized  2y_difference_in_annualized  \
date                                                                   
1969-12-31                          NaN                          NaN   
1970-01-30                          NaN                          NaN   
1970-02-27                          NaN                          NaN   
1970-03-31                          NaN                          NaN   
1970-04-30                          NaN                          NaN   
1970-05-29                          NaN                          NaN   
1970-06-30                          NaN                          NaN   
1970-07-31                          NaN                          NaN   
1970-08-31                          NaN                          NaN   
1970-09-30                          NaN                          NaN   

            3y_difference_in_annualized  5y_difference_in_annualized  \
date                                                                   
1969-12-31                          NaN                          NaN   
1970-01-30                          NaN                          NaN   
1970-02-27                          NaN                          NaN   
1970-03-31                          NaN                          NaN   
1970-04-30                          NaN                          NaN   
1970-05-29                          NaN                          

In [157]:
msci_world.describe()

price         ffr   sgd_ir_1m  1m_cumulative  3m_cumulative  \
count    644.000000  644.000000  430.000000     643.000000     641.000000   
mean    2594.949079    5.193560    1.693506       0.008345       0.025404   
std     2774.782088    4.284294    1.639291       0.043085       0.077230   
min       81.167249    0.048345    0.016769      -0.189471      -0.331688   
25%      284.248573    1.449395    0.305900      -0.016201      -0.012162   
50%     1734.370923    5.140584    1.247290       0.012068       0.029091   
75%     3752.326277    7.405355    2.717513       0.033158       0.071651   
max    11779.930720   23.069445    8.023426       0.146480       0.306124   

       6m_cumulative  1y_cumulative  2y_cumulative  3y_cumulative  \
count     638.000000     632.000000     620.000000     608.000000   
mean        0.052222       0.107926       0.229144       0.357783   
std         0.115410       0.172027       0.273751       0.367235   
min        -0.434646      -0.469420      -0.470921      -0.453187   
25%        -0.012556       0.011797       0.084944       0.168612   
50%         0.056267       0.124587       0.248725       0.338780   
75%         0.115870       0.203605       0.371642       0.533052   
max         0.469370       0.665528       1.388766       2.002092   

       5y_cumulative  ...  6m_difference_in_annualized  \
count     584.000000  ...                   638.000000   
mean        0.662486  ...                     0.053587   
std         0.609324  ...                     0.126325   
min        -0.246839  ...                    -0.326187   
25%         0.233656  ...                    -0.020120   
50%         0.596080  ...                     0.048074   
75%         0.897247  ...                     0.119599   
max         3.358870  ...                     0.654640   

       1y_difference_in_annualized  2y_difference_in_annualized  \
count                   632.000000                   620.000000   
mean                      0.050055                     0.048457   
std                       0.096169                     0.071302   
min                      -0.341127                    -0.169207   
25%                      -0.002096                     0.011260   
50%                       0.052235                     0.055046   
75%                       0.102225                     0.087927   
max                       0.395450                     0.290696   

       3y_difference_in_annualized  5y_difference_in_annualized  \
count                   608.000000                   584.000000   
mean                      0.046828                     0.044451   
std                       0.057427                     0.042836   
min                      -0.117029                    -0.062831   
25%                       0.019328                     0.022417   
50%                       0.052713                     0.046539   
75%                       0.080876                     0.067390   
max                       0.206713                     0.163371   

       10y_difference_in_annualized  15y_difference_in_annualized  \
count                    524.000000                    464.000000   
mean                       0.043439                      0.041535   
std                        0.026155                      0.021004   
min                       -0.017469                     -0.004205   
25%                        0.026242                      0.027052   
50%                        0.045028                      0.039538   
75%                        0.059556                      0.058166   
max                        0.108481                      0.090286   

       20y_difference_in_annualized  25y_difference_in_annualized  \
count                    404.000000                    344.000000   
mean                       0.041967                      0.042586   
std                        0.016375                      0.011690   
min                        0.003932                      0.018381   


In [158]:
msci_world.loc[:, [*msci_world.loc[:,'1m_annualized':'30y_annualized'].columns, *msci_world.loc[:,'1m_dca_annualized':'30y_dca_annualized']]].describe()

1m_annualized  3m_annualized  6m_annualized  1y_annualized  \
count     643.000000     641.000000     638.000000     632.000000   
mean        0.235290       0.142417       0.120470       0.107926   
std         0.615503       0.330995       0.240850       0.172027   
min        -0.919606      -0.800512      -0.680375      -0.469420   
25%        -0.177990      -0.047767      -0.024953       0.011797   
50%         0.154822       0.121542       0.115701       0.124587   
75%         0.479120       0.318907       0.245166       0.203605   
max         4.157034       1.910296       1.159047       0.665528   

       2y_annualized  3y_annualized  5y_annualized  10y_annualized  \
count     620.000000     608.000000     584.000000      524.000000   
mean        0.101734       0.098529       0.096603        0.098103   
std         0.123897       0.098712       0.074655        0.047746   
min        -0.272622      -0.182264      -0.055118       -0.023284   
25%         0.041607       0.053311       0.042891        0.067916   
50%         0.117463       0.102139       0.098022        0.092439   
75%         0.171171       0.153061       0.136645        0.131988   
max         0.545563       0.442585       0.342378        0.207729   

       15y_annualized  20y_annualized  ...  6m_dca_annualized  \
count      464.000000      404.000000  ...         638.000000   
mean         0.097693        0.096237  ...           0.066883   
std          0.041045        0.032417  ...           0.146481   
min          0.030301        0.034885  ...          -0.511905   
25%          0.062957        0.067823  ...          -0.008372   
50%          0.087821        0.093441  ...           0.069936   
75%          0.141787        0.125016  ...           0.153138   
max          0.181283        0.158232  ...           0.578531   

       1y_dca_annualized  2y_dca_annualized  3y_dca_annualized  \
count         632.000000         620.000000         608.000000   
mean            0.057871           0.053277           0.051701   
std             0.100789           0.072046           0.058078   
min            -0.355105          -0.244855          -0.169605   
25%             0.005266           0.019169           0.022129   
50%             0.069333           0.065479           0.059007   
75%             0.114416           0.093732           0.084341   
max             0.375042           0.291650           0.259507   

       5y_dca_annualized  10y_dca_annualized  15y_dca_annualized  \
count         584.000000          524.000000          464.000000   
mean            0.052153            0.054664            0.056158   
std             0.044528            0.029623            0.026661   
min            -0.087035           -0.030160           -0.007516   
25%             0.026288            0.035443            0.036857   
50%             0.051326            0.052285            0.049256   
75%             0.074450            0.068951            0.079087   
max             0.201618            0.139881            0.111740   

       20y_dca_annualized  25y_dca_annualized  30y_dca_annualized  
count          404.000000          344.000000          284.000000  
mean             0.054270            0.053804            0.053177  
std              0.022221            0.019260            0.013362  
min              0.007972            0.022705            0.034718  
25%              0.036551            0.037448            0.042624  
50%              0.046098            0.047641            0.046903  
75%              0.080450            0.067424            0.066073  
max              0.093196            0.094058            0.088595  

[8 rows x 24 columns]

In [159]:
go.Figure(
    data = [
        go.Box(
            x=msci_world[column],
            name=column,
            )
        for column in msci_world.loc[:,'1m_annualized':'30y_annualized'].columns
    ],
    layout = go.Layout(
        height=800,
        xaxis=dict(
            tickformat='.2%',
        )
    )
)

In [160]:
go.Figure(
    data = [
        go.Box(
            x=msci_world[column],
            name=column,
            )
        for column in chain.from_iterable(zip(msci_world.loc[:,'1m_annualized':'30y_annualized'].columns, msci_world.loc[:,'1m_dca_annualized':'30y_dca_annualized']))
    ],
    layout = go.Layout(
        height=800,
        xaxis=dict(
            tickformat='.2%',
        )
    )
)

In [161]:
go.Figure(
    [
        go.Scatter(
            x=msci_world.index,
            y=msci_world[column],
            name=column,
            mode='lines'
            )
        for column in ['5y_annualized', '5y_dca_annualized']
    ],
    layout = go.Layout(
        yaxis=dict(
            tickformat='.0%',
        )
    )
)

In [162]:
go.Figure(
    [
        go.Scatter(
            x=msci_world.index,
            y=msci_world[column],
            name=column,
            mode='lines'
            )
        for column in ['10y_annualized', '10y_dca_annualized']
    ],
    layout = go.Layout(
        yaxis=dict(
            tickformat='.0%',
        )
    )
)

In [163]:
go.Figure(
    [
        go.Scatter(
            x=msci_world.index,
            y=msci_world[column],
            name=column,
            mode='lines'
            )
        for column in ['20y_annualized', '20y_dca_annualized']
    ],
    layout = go.Layout(
        yaxis=dict(
            tickformat='.0%',
        )
    )
)

In [164]:
go.Figure(
    [
        go.Box(
            x=msci_world[column],
            name=column,
            opacity=0.75
            )
        for column in msci_world.loc[:, '1m_difference_in_annualized':'30y_difference_in_annualized'].columns
    ],
    layout = go.Layout(
        xaxis=dict(
            tickformat='.0%',
        )
    )
)

In [182]:
shy = yf.download('SHY')
iei = yf.download('IEI')
ief = yf.download('IEF')
tlt = yf.download('TLT')

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed


In [183]:
from typing import Literal

In [184]:
from pandas.tseries.offsets import BMonthEnd

In [185]:
def load_us_treasury_rate(duration: Literal['1MO', '3MO', '6MO', '1', '2', '3', '5', '7', '10', '20', '30']):
    try:
        treasury_rate = pd.read_csv(f'data/us_treasury_{duration.lower()}.csv', parse_dates=['date'])
        if pd.to_datetime(treasury_rate['date']).iloc[-1] < pd.to_datetime('today') + BMonthEnd(-1, 'D'):
            raise FileNotFoundError
        treasury_rate = treasury_rate.set_index('date')['rate']
    
    except FileNotFoundError:
        treasury_rate = download_us_treasury_rate(duration)
        treasury_rate.to_csv(f'data/us_treasury_{duration.lower()}.csv')
    
    treasury_rate = treasury_rate.resample('D').last().reset_index().set_index('date')
    treasury_rate['rate'] = np.select(
        [
            (treasury_rate['rate'].ffill() > treasury_rate['rate'].bfill()).values,
            (treasury_rate['rate'].ffill() < treasury_rate['rate'].bfill()).values
            ],
        [
            treasury_rate['rate'].ffill().values,
            treasury_rate['rate'].bfill().values
            ],
        treasury_rate['rate'].ffill().values
        )

    return treasury_rate

In [442]:
def load_us_treasury_returns(duration: Literal['1MO', '3MO', '6MO', '1', '2', '3', '5', '7', '10', '20', '30']):
    treasury = load_us_treasury_rate(duration)
    treasury['old_issue_start_price'] = np.exp(treasury['rate'].div(36000).mul(-365.25*int(duration))).shift()
    treasury['old_issue_end_price'] = np.exp(treasury['rate'].div(36000).mul(1-365.25*int(duration)))
    treasury['change'] = treasury['old_issue_end_price'].div(treasury['old_issue_start_price'])
    treasury['price'] = np.exp(np.log(treasury['change']).cumsum()).fillna(1)
    
    return treasury

In [443]:
treasury = (pd.concat([load_us_treasury_returns(duration)['price'].rename(duration) for duration in ['1', '2', '3', '5', '7', '10', '20', '30']], axis=1)
            .merge(np.exp(np.log(fed_funds_rate.loc['2007':].div(36000).add(1)).cumsum()).fillna(1), left_index=True, right_index=True)
            .merge(shy['Adj Close'].rename('SHY'), left_index=True, right_index=True)
            .merge(iei['Adj Close'].rename('IEI'), left_index=True, right_index=True)
            .merge(ief['Adj Close'].rename('IEF'), left_index=True, right_index=True)
            .merge(tlt['Adj Close'].rename('TLT'), left_index=True, right_index=True)
)

In [445]:
treasury

1          2          3          5          7         10  \
2007-01-11  21.082610  10.361250  23.907922  24.768717  21.248581  23.614957   
2007-01-12  21.083696  10.358563  23.889519  24.734483  21.206236  23.546288   
2007-01-16  21.096601  10.368837  23.917738  24.773322  21.247907  23.606532   
2007-01-17  21.095559  10.359848  23.892067  24.726548  21.190520  23.514032   
2007-01-18  21.100933  10.365575  23.917309  24.767637  21.238596  23.612750   
...               ...        ...        ...        ...        ...        ...   
2023-08-11  27.888270  14.002380  33.266273  36.648426  33.059719  38.590006   
2023-08-14  27.898961  13.988745  33.199146  36.569587  33.001506  38.486066   
2023-08-15  27.906293  14.002170  33.203739  36.574255  32.958728  38.412510   
2023-08-16  27.907971  13.990055  33.167964  36.467817  32.822683  38.145171   
2023-08-17  27.915305  14.000649  33.182680  36.472533  32.803488  38.072362   

                   20         30       ffr        shy         iei        ief  \
2007-01-11  17.275286  19.140535  1.001602  63.444092   74.377457  55.757725   
2007-01-12  17.137731  18.910892  1.001747  63.404442   74.384956  55.642658   
2007-01-16  17.215828  18.976482  1.002330  63.467869   74.310524  55.750919   
2007-01-17  17.078755  18.805971  1.002476  63.444092   74.303108  55.642658   
2007-01-18  17.220036  18.980462  1.002622  63.467869   74.370087  55.717102   
...               ...        ...       ...        ...         ...        ...   
2023-08-11  29.194709  32.608181  1.204342  80.970001  114.309998  94.129997   
2023-08-14  29.144999  32.418925  1.204877  80.900002  114.099998  93.980003   
2023-08-15  28.971280  32.127130  1.205056  80.930000  114.059998  93.800003   
2023-08-16  28.623866  31.548616  1.205234  80.889999  113.839996  93.440002   
2023-08-17  28.453324  31.264732  1.205413  80.980003  113.900002  93.320000   

                  TLT  
2007-01-11  54.345570  
2007-01-12  54.093670  
2007-01-16  54.210442  
2007-01-17  54.044544  
2007-01-18  54.210442  
...               ...  
2023-08-11  95.370003  
2023-08-14  95.160004  
2023-08-15  94.580002  
2023-08-16  93.839996  
2023-08-17  93.440002  

[4179 rows x 13 columns]

In [446]:
treasury.div(treasury.iloc[0]).plot.line().update_yaxes(type='log')